In [1]:
include("analysis_fcns.jl")

best_fit_params (generic function with 2 methods)

In [2]:
using SimplePlots

HTML{String}("  <script type=\"text/javascript\" class=\"js-plotly-script\">\n    globalComms = {};\n    demoData = {};\n\n    \$(\".js-plotly-script\").parent().css('padding', 0);\n\n    function customPlotlyReact(curPlot, curData, curLayout, curConfig) {\n      for (var i = 0; i < curData.length; i++) {\n        curData[i][\"visible\"] = true;\n        for (var j = 0; j < curPlot.data.length; j++) {\n          if ( curData[i].name !== curPlot.data[j].name ) { continue; }\n          if ( curPlot.data[j].visible !== \"legendonly\" ) { continue; }\n\n          curData[i][\"visible\"] = \"legendonly\";\n        }\n      }\n\n      Plotly.react(curPlot, curData, curLayout, curConfig);\n    }\n\n    function customPlotLoader(curCallback) {\n      if ( \$(\".js-nouislider-css\").length == 0 ) {\n        \$(\"head\").append(\n          '<link class=\"js-nouislider-css\" href=\"https://cdn.jsdelivr.net/gh/djsegal/SimplePlots.jl/dist/nouislider.min.css\" rel=\"stylesheet\">'\n        );\n      }\n\n      if ( \$(\".js-custom-css\").length == 0 ) {\n        \$(\"head\").append(\n          '<link class=\"js-custom-css\" href=\"https://cdn.jsdelivr.net/gh/djsegal/SimplePlots.jl/dist/custom.min.css\" rel=\"stylesheet\">'\n        );\n      }\n\n      if ( typeof Plotly !== \"undefined\" ) {\n        if ( typeof curCallback !== \"undefined\" ) {\n          curCallback();\n        }\n        return;\n      }\n\n      var plotlyScripts = document.getElementsByClassName(\"js-plotly-script\");\n\n      for (var i = 0; i < plotlyScripts.length; i++) {\n        var scriptParent = plotlyScripts[i].parentElement;\n        scriptParent.style.margin = \"0\";\n        scriptParent.style.padding = \"0\";\n      }\n\n      require.config({\n        paths: {\n          Plotly: \"https://cdn.plot.ly/plotly-1.53.0.min\",\n          noUiSlider: \"https://cdn.jsdelivr.net/gh/djsegal/SimplePlots.jl/dist/nouislider.min\",\n          wNumb: \"https://cdn.jsdelivr.net/gh/djsegal/SimplePlots.jl/dist/wnumb.min\"\n        }\n      });\n\n      require([\"Plotly\", \"noUiSlider\", \"wNumb\"], function(Plotly, noUiSlider, wNumb){\n        window.Plotly = Plotly;\n        window.noUiSlider = noUiSlider;\n        window.wNumb = wNumb;\n\n        if ( typeof curCallback !== \"undefined\" ) {\n          curCallback();\n        }\n\n        \$(\"head\").append(\$(\".js-plotly-script\"));\n        \$(\"head .js-plotly-script:not(:first)\").remove();\n        \$(\"body .js-plotly-script\").remove();\n      });\n    }\n\n    \$(document).ready(customPlotLoader);\n    customPlotLoader();\n  </script>\n")

In [3]:
dosfiles = string.("DOSes/", readdir("./DOSes/"))
electrode_surfaces = [dosfile[7:end-7] for dosfile in dosfiles]

3-element Array{String,1}:
 "Cu111"
 "LiF_Li2CO3"
 "Li_100_"

In [12]:
#@demo for Ef_eq=-2.0:0.05:1.0, λ=0.05:0.01:0.5, T=100:20:400, electrode_surface=electrode_surfaces, show_electrolyte_DOS=true
@demo for Ef_eq in -2.0:0.05:1.0, λ in 0.05:0.01:0.5
    T = 300
    #λ = 0.3
    electrode_surface = electrode_surfaces[1]
    show_electrolyte_DOS = true
    kT = 8.617e-5*T
    dosfile = string("DOSes/", electrode_surface, "dos.txt")
    dos_f, average_dos, min_E, max_E = get_dos(dosfile; Ef=Ef_eq)
    if occursin("Li_1",electrode_surface)
        E_range=1.5
    else
        E_range=4
    end
    E_vals = range(-E_range, E_range, length=500)
    dos_vals=dos_f.(E_vals)
    fd_vals_e = fermi_dirac.(E_vals; kT=kT)
    fd_vals_h = 1 .- fd_vals_e
    dos_vals_e = fd_vals_e .* dos_vals
    dos_vals_h = fd_vals_h .* dos_vals

    ox_dos_vals = 0.5.*maximum(dos_vals).*marcus_integrand.(E_vals, λ, 0, true; kT=kT)
    red_dos_vals = 0.5.*maximum(dos_vals).*marcus_integrand.(E_vals, λ, 0, false; kT=kT)
    #p1 = plot(E_vals, hcat(dos_vals_e, dos_vals_h, ox_dos_vals, red_dos_vals), label=["electrons" "holes" "reduction" "oxidation"], title="Electrode state occupations", xlabel="E-E_f", ylabel="# (arb.)", color=[:blue :orange :blue :orange], linestyle=[:solid :solid :dash :dash])
    plot(E_vals, dos_vals_e, label="electrons")
    plot!(E_vals, dos_vals_h, label="holes")
    plot!(E_vals, ox_dos_vals, label="reduction")
    plot!(E_vals, red_dos_vals, label="oxidation")
end

HTML{String}("  <div class='js-interact' id='js-interact__dedcba93-464d-4ba0-a175-b60e032697f9'>\n    <div class='js-widgets'>\n  <div class='cs-widget js-widget'>\n    <div class='cs-widget-label'>\n      Ef_eq\n    </div>\n<div class='cs-widget-slider js-widget-slider'></div>  <div class='cs-widget-value js-widget-value '>\n    -0.5\n  </div>\n\n  </div>\n    </div>\n\n    <div class='js-display'>\n    </div>\n  </div>\n  <script>\n    var anonFunc = function () {\n  var foundSlider = false;\n  \$(\"#js-interact__dedcba93-464d-4ba0-a175-b60e032697f9 .js-widget-slider\").each(function( index ) {\n    var tmpText = \$(this.parentElement).children(\".cs-widget-label\").text().trim();\n    if ( tmpText !== \"Ef_eq\" ) { return; }\n\n    if ( foundSlider ) { alert(\"There are repeated sliders!\"); }\n\n    foundSlider = true;\n    noUiSlider.create(this, {\n        start: 30,\n        step: 1,\n        connect: \"lower\",\n        format: wNumb({\n          decimals: 0\n        }),\n        range: {\n          min: 0,\n          max: 60\n        }\n    });\n\n    var that = this;\n    this.noUiSlider.on('update', function (values, handle) {\n      var tmpRange = [\"-2.0\", \"-1.95\", \"-1.9\", \"-1.85\", \"-1.8\", \"-1.75\", \"-1.7\", \"-1.65\", \"-1.6\", \"-1.55\", \"-1.5\", \"-1.45\", \"-1.4\", \"-1.35\", \"-1.3\", \"-1.25\", \"-1.2\", \"-1.15\", \"-1.1\", \"-1.05\", \"-1.0\", \"-0.95\", \"-0.9\", \"-0.85\", \"-0.8\", \"-0.75\", \"-0.7\", \"-0.65\", \"-0.6\", \"-0.55\", \"-0.5\", \"-0.45\", \"-0.4\", \"-0.35\", \"-0.3\", \"-0.25\", \"-0.2\", \"-0.15\", \"-0.1\", \"-0.05\", \"0.0\", \"0.05\", \"0.1\", \"0.15\", \"0.2\", \"0.25\", \"0.3\", \"0.35\", \"0.4\", \"0.45\", \"0.5\", \"0.55\", \"0.6\", \"0.65\", \"0.7\", \"0.75\", \"0.8\", \"0.85\", \"0.9\", \"0.95\", \"1.0\"];\n      var newValue = tmpRange[values[handle]];\n\n      var tmpSpan = \$(that.parentElement).children(\".js-widget-value\")[0];\n      tmpSpan.innerText = newValue;\n\n      \$(\"#js-interact__dedcba93-464d-4ba0-a175-b60e032697f9\").trigger(\"interact\");\n    });\n  });\n  if ( !foundSlider ) { alert(\"Unable to find all sliders!\"); }\n  \$(\".js-widget-toggle .cs-button\").click(function (curEvent) {\n    if ( !\$(curEvent.target).hasClass(\"cs-active\") ) {\n      var curItems = \$(curEvent.target.parentElement).children(\".cs-button\");\n      var curIndex = curItems.index(curEvent.target);\n\n      \$.each(curItems, function(workIndex, workValue) {\n        var otherTarget = \$(curEvent.target.parentElement.children[workIndex]);\n\n        otherTarget.removeClass(\"cs-active\");\n        otherTarget.removeClass(\"cs-pre-active\");\n\n        if ( workIndex == curIndex ) { otherTarget.addClass(\"cs-active\"); }\n        if ( workIndex == curIndex - 1 ) { otherTarget.addClass(\"cs-pre-active\"); }\n      });\n\n      var curWidgetVal = \$(curEvent.target).closest(\".js-widget\").children(\".js-widget-value\")[0];\n      curWidgetVal.innerText = curEvent.target.innerText;\n\n      \$(\"#js-interact__dedcba93-464d-4ba0-a175-b60e032697f9\").trigger(\"interact\");\n    }\n  });\n  \$(\"#js-interact__dedcba93-464d-4ba0-a175-b60e032697f9\").on(\"interact\", function() {\n    var msgLabels = \$(\"#js-interact__dedcba93-464d-4ba0-a175-b60e032697f9 .cs-widget-label\").map(function(){\n       return \$.trim(\$(this).text());\n    }).get();\n\n    var msgValues = \$(\"#js-interact__dedcba93-464d-4ba0-a175-b60e032697f9 .cs-widget-value\").map(function(){\n       return \$.trim(\$(this).text());\n    }).get();\n\n    var msgDict = msgLabels.reduce((obj, k, i) => ({...obj, [k]: msgValues[i] }), {});\n\n    var workPlotlyId = \$(\"#js-interact__dedcba93-464d-4ba0-a175-b60e032697f9 .js-plotly-plot\").attr(\"id\");\n    msgDict[\"___interact_plot_id___\"] = workPlotlyId;\n\n    if ( \"interact-dedcba93-464d-4ba0-a175-b60e032697f9\" in demoData ) {\n      tmpData = demoData[\"interact-dedcba93-464d-4ba0-a175-b60e032697f9\"];\n  tmpData = tmpData[msgDict[\"Ef_eq\"]];\n      va